# Loading data if you need.

In [1]:
#1
import re
import numpy as np
import glob

import random
import matplotlib.pyplot as plt

import pandas as pd
from urllib.request import urlopen
import numpy as np
from lxml import etree

import pandas as pd
from urllib.request import urlopen
import numpy as np
from lxml import etree

In [5]:
# saving numarray(ndarray)
x_train_positive_all = np.load('../saving_numpy_array/v8-16/x_train/all/x_train_positive_all_v8-16.npy')
y_train_positive_all = np.load('../saving_numpy_array/v8-16/x_train/all/y_train_positive_all_v8-16.npy')
x_train_positive_all_5crossval = np.load('../saving_numpy_array/v8-16/x_train/all/x_train_positive_all_5crossval_v8-16.npy')
y_train_positive_all_5crossval = np.load('../saving_numpy_array/v8-16/x_train/all/y_train_positive_all_5crossval_v8-16.npy')

In [6]:
'''
#loding ndarray
print(type(np.load('../saving_numpy_array/v8-16/x_train/all/x_train_all_v8-16_only_positive.npy')))
print(np.load('../saving_numpy_array/v8-16/x_train/all/x_train_all_v8-16_only_positive.npy'))

x_train_positive_all = np.load('../saving_numpy_array/v8-16/x_train/all/x_train_all_v8-16_only_positive.npy')
y_train_all = np.load('../saving_numpy_array/v8-16/x_train/all/y_train_all_v8-16_only_positive.npy')
x_train_all_5crossval = np.load('../saving_numpy_array/v8-16/x_train/all/x_train_all_ 5crossval_v8-16_only_positive.npy')
y_train_all_5crossval = np.load('../saving_numpy_array/v8-16/x_train/all/y_train_all_5crossval_v8-16_only_positive.npy')
#y_train_all_5crossval_v8-1_only_positive

SyntaxError: EOF while scanning triple-quoted string literal (<ipython-input-6-21c1036cf3b0>, line 10)

In [7]:
print(len(x_train_positive_all))
print(len(x_train_positive_all_5crossval))
print(len(y_train_positive_all))
print(len(y_train_positive_all_5crossval))
#print(subs_sum)

166
41
166
41


In [8]:
print(len(x_train_positive_all[0]))

14


# creating negative data

今回の配列前処理のクラスを作った方がいいな．毎回同じ関数をファイルごとに書かないといけなくなっている．

positive dataはUniprot IDがなくてもMEROPSに記載の開裂部位を正解データとして用いることができるが，negative dataはUniprot IDがないと開裂部位意外の箇所を指定できないのと，開裂部位に一致する箇所が複数あった場合，それらを含む箇所を除外する手順を設定する必要がある．

### main()に必要な関数たちを再度定義．

In [9]:
#ここからはじまる．
import mysql.connector as mydb

# コネクションの作成
conn = mydb.connect(
    host='localhost',
    port='3306',
    user='3a16057',
    password='TuWqAc4#97',
    database='meropsrefs01'
)

In [10]:
# DB操作用にカーソルを作成
cur = conn.cursor()

In [11]:
positive_proteases_txt = {"HAT":"S01-047(human_airway_trypsin-like_peptidase).txt", "DESC1":"S01-021(DESC1_peptidase).txt",  
                      "TMPRSS2":"S01-247(epitheliasin).txt", "TMPRSS4":"S01-034(transmembrane_peptidase-serine_4).txt"}

In [12]:
uid_eg = 'P78365'

def aaseq_from_uid(uid, substrate_turn, index):
    df = pd.DataFrame(np.arange(3).reshape(1, 3), columns=['uniprotKB_accession', 'function', 'sequence'], index=['protease'+str(substrate_turn)+'_substrate'+str(index)])

    for column_name in df:
        df[column_name] = df[column_name].astype(str)

    df['uniprotKB_accession'][0] = uid

    #display(df)    

    url = "https://www.uniprot.org/uniprot/" + uid + ".xml"
    f = urlopen(url)
    xml = f.read()
    root = etree.fromstring(xml)
    
    #以下のコードは下の説明を参照
    function = root.find('./entry/comment[@type="function"]', root.nsmap)
    if function==None:
        print("function was not detected.")
        pass
    else:
        df["function"][0] = function[0].text
        #print(function[0].text+"¥n")

    sequence = root.find('./entry/sequence', root.nsmap) 
    if sequence==None: 
        print("sequence was not detected.")
        pass 
    else: 
        df["sequence"][0] = sequence.text 
        #print(sequence.text+"¥n")

    #display(df) 
    #df0=pd.concat([df0, df], axis=0)
    #display(df0)
    display(df) 
    return df["sequence"][0]

In [13]:
def get_cleave_point(fullaa, cleave_pattern):
    #cleave_point=-1
    p4=-1
    cleave_points = []

    print(cleave_pattern)
    cleave_pattern02 = re.sub("-", "[A-Z]{1}", cleave_pattern)
    print(cleave_pattern02)
    
    for w in range(len(fullaa)-8):
        if re.search(cleave_pattern02, fullaa[w:w+8]):
            cleave_point = w
            cleave_points.append(w)
            print(cleave_points)
            print("cleave_point: " + str(cleave_point))
            continue
    #print(twenty_aa)
    print(f'cleave_point_list: {cleave_points}')
    if cleave_points:
        p4 = cleave_points[0]
    if p4 == -1:
        print("there is no cleave_pattern.")
    else:
        pass
    return p4, cleave_points

In [14]:
def get_negative_data_seq(fullaa, cleave_point_list):
    cleave_range_list = []
    negative_eight_aa_list = []
    
    for s in range(len(cleave_point_list)):
        point = cleave_point_list[s]
        for t in range(-7, 8, 1):
            cleave_range_list.append(point+t)
        print(cleave_range_list)
    
    for s in range(len(cleave_point_list)):
        np.random.seed(0)
        a = np.arange(len(fullaa)-8)

        np.random.shuffle(a)
        print(a)

        t = 0
        while 1:
            if a[t] not in cleave_range_list:
                rdm = a[t]
                break
            else:
                t = t + 1
        negative_eight_aa = fullaa[rdm:rdm+8]
        negative_eight_aa_list.append(negative_eight_aa)
    return negative_eight_aa_list

In [15]:
# マッチパターンが複数あることを探す関数．
def search_double_pattern(fullaa, cleave_pattern):
    cleave_point=-1
    match_pattern_count = 0
    if "-" in cleave_pattern:
        cleave_pattern02 = re.sub("-", "[A-Z]{1}", cleave_pattern)
        for i in range(len(fullaa)-7):
            if re.search(cleave_pattern02, fullaa[i:i+8]) != None:
                cleave_point = i
                match_pattern_count = match_pattern_count + 1
                print("cleave_point: " + str(cleave_point))
                continue
    else:
        for i in range(len(fullaa)-7):
            #print(fullaa[i:i+8])
            if fullaa[i:i+8] == cleave_pattern:
                cleave_point = i
                match_pattern_count = match_pattern_count + 1
                print("cleave_point: " + str(cleave_point))
                continue
    return match_pattern_count

In [16]:
def get_cleave_pattern(p4_column):
    seq = ""
    three_aa = ""
    for j in range(8):
        three_aa = str(df.iloc[i, p4_column+j])
        print(f'three_aa: {three_aa}')
        
        #print(one_aa) 
        if three_aa == "Ala":
            one_aa = "A"
        elif three_aa == "Cys":
            one_aa = "C"
        elif three_aa == "Asp":
            one_aa = "D"
        elif three_aa == "Glu":
            one_aa = "E"
        elif three_aa == "Phe":
            one_aa = "F"
        elif three_aa == "Gly":
            one_aa = "G"
        elif three_aa == "His":
            one_aa = "H"
        elif three_aa == "Ile":
            one_aa = "I"
        elif three_aa == "Lys":
            one_aa = "K"
        elif three_aa == "Leu":
            one_aa = "L"
        elif three_aa == "Met":
            one_aa = "M"
        elif three_aa == "Asn":
            one_aa = "N"
        elif three_aa == "Pro":
            one_aa = "P"
        elif three_aa == "Gln":
            one_aa = "Q"
        elif three_aa == "Arg":
            one_aa = "R"
        elif three_aa == "Ser":
            one_aa = "S"
        elif three_aa == "Thr":
            one_aa = "T"
        elif three_aa == "Val":
            one_aa = "V"
        elif three_aa == "Trp":
            one_aa = "W"
        elif three_aa == "Tyr":
            one_aa = "Y"
        else:
            print("This is not a major amino acid or \"- \".")
            print(f'This is {three_aa}.')
            one_aa = "-"
            pass 
        print(f'one_aa: {one_aa}')
        seq = seq + one_aa
    print("cleave_pattern: "+seq)
    return seq

In [17]:
def aa_charge(e, cleave_pattern):
    for j in range(8):   
        one_char_aa = cleave_pattern[j]
        if one_char_aa == "A":
            x_train[e][0][j][0] = charge["A"]
        elif one_char_aa == "C":
            x_train[e][0][j][0] = charge["C"]
        elif one_char_aa == "D":
            x_train[e][0][j][0] = charge["D"]
        elif one_char_aa == "E":
            x_train[e][0][j][0] = charge["E"]
        elif one_char_aa == "F":
            x_train[e][0][j][0] = charge["F"]
        elif one_char_aa == "G":
            x_train[e][0][j][0] = charge["G"]
        elif one_char_aa == "H":
            x_train[e][0][j][0] = charge["H"]
        elif one_char_aa == "I":
            x_train[e][0][j][0] = charge["I"]
        elif one_char_aa == "K":
            x_train[e][0][j][0] = charge["K"]
        elif one_char_aa == "L":
            x_train[e][0][j][0] = charge["L"]
        elif one_char_aa == "M":
            x_train[e][0][j][0] = charge["M"]
        elif one_char_aa == "N":
            x_train[e][0][j][0] = charge["N"]
        elif one_char_aa == "P":
            x_train[e][0][j][0] = charge["P"]
        elif one_char_aa == "Q":
            x_train[e][0][j][0] = charge["Q"]
        elif one_char_aa == "R":
            x_train[e][0][j][0] = charge["R"]
        elif one_char_aa == "S":
            x_train[e][0][j][0] = charge["S"]
        elif one_char_aa == "T":
            x_train[e][0][j][0] = charge["T"]
        elif one_char_aa == "V":
            x_train[e][0][j][0] = charge["V"]
        elif one_char_aa == "W":
            x_train[e][0][j][0] = charge["W"]
        elif one_char_aa == "Y":
            x_train[e][0][j][0] = charge["Y"]
        else:
            pass

In [18]:
def aa_hypho(e, cleave_pattern):
    for j in range(8):
        one_char_aa = cleave_pattern[j]
        if one_char_aa == "A":
            x_train[e][1][j][0] = hydrophobicity["A"]
        elif one_char_aa == "C":
            x_train[e][1][j][0] = hydrophobicity["C"]
        elif one_char_aa == "D":
            x_train[e][1][j][0] = hydrophobicity["D"]
        elif one_char_aa == "E":
            x_train[e][1][j][0] = hydrophobicity["E"]
        elif one_char_aa == "F":
            x_train[e][1][j][0] = hydrophobicity["F"]
        elif one_char_aa == "G":
            x_train[e][1][j][0] = hydrophobicity["G"]
        elif one_char_aa == "H":
            x_train[e][1][j][0] = hydrophobicity["H"]
        elif one_char_aa == "I":
            x_train[e][1][j][0] = hydrophobicity["I"]
        elif one_char_aa == "K":
            x_train[e][1][j][0] = hydrophobicity["K"]
        elif one_char_aa == "L":
            x_train[e][1][j][0] = hydrophobicity["L"]
        elif one_char_aa == "M":
            x_train[e][1][j][0] = hydrophobicity["M"]
        elif one_char_aa == "N":
            x_train[e][1][j][0] = hydrophobicity["N"]
        elif one_char_aa == "P":
            x_train[e][1][j][0] = hydrophobicity["P"]
        elif one_char_aa == "Q":
            x_train[e][1][j][0] = hydrophobicity["Q"]
        elif one_char_aa == "R":
            x_train[e][1][j][0] = hydrophobicity["R"]
        elif one_char_aa == "S":
            x_train[e][1][j][0] = hydrophobicity["S"]
        elif one_char_aa == "T":
            x_train[e][1][j][0] = hydrophobicity["T"]
        elif one_char_aa == "V":
            x_train[e][1][j][0] = hydrophobicity["V"]
        elif one_char_aa == "W":
            x_train[e][1][j][0] = hydrophobicity["W"]
        elif one_char_aa == "Y":
            x_train[e][1][j][0] = hydrophobicity["Y"]
        else:
            pass    

In [19]:
#https://trade-and-develop.hatenablog.com/entry/2017/02/23/021119
cur = conn.cursor(buffered=True)

In [20]:
#adding secoundary structure
def add_secondary_structure(e, uid, p4, cleave_pattern):
    uid = [uid]
    cur.execute("SELECT substrate_2d FROM substrate_2d where uniprot_acc=(%s);", uid)  
    ss = cur.fetchall()
    if not ss:
        print("substrate_2d is empty.")
        return 0    
    else:
        print(ss)
    ssl=list(ss[0][0])

    for j in range(8):
        one_char_aa = cleave_pattern[j]
        if p4-1 +j < 0:
            continue
        if p4-1+j > len(ssl)-1:
            return 0
        if ssl[p4-1 + j] == 'a':
            x_train[e][2][j][0]= 1
        elif ssl[p4-1 + j] =='b':
            x_train[e][3][j][0] = 1
        else:
            pass 
    return 1

In [21]:
'''backup
#adding secoundary structure
def add_secoundary_structure(e, uid, p4, cleave_pattern):
    uid = [uid]
    cur.execute("SELECT substrate_2d FROM substrate_2d where uniprot_acc=(%s);", uid)  
    ss = cur.fetchall()
    if not ss:
        print("substrate_2d is empty.")
        return 0    
    else:
        print(ss)
    ssl=list(ss[0][0])

    for j in range(8):
        one_char_aa = cleave_pattern[j]
        if p4-1 +j < 0:
            continue
        if p4-1+j > len(ssl)-1:
            return 0
        if ssl[p4-1 + j] == 'a':
            if one_char_aa == "A":
                x_train[e][2][j][0]= 1
            elif one_char_aa == "C":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "D":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "E":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "F":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "G":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "H":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "I":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "K":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "L":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "M":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "N":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "P":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "Q":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "R":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "S":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "T":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "V":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "W":
                x_train[e][2][j][0] = 1
            elif one_char_aa == "Y":
                x_train[e][2][j][0] = 1
        elif ssl[p4-1 + j] =='b':
            if one_char_aa == "A":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "C":
                x_train[e][3][j][0] =1
            elif one_char_aa == "D":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "E":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "F":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "G":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "H":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "I":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "K":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "L":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "M":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "N":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "P":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "Q":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "R":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "S":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "T":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "V":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "W":
                x_train[e][3][j][0] = 1
            elif one_char_aa == "Y":
                x_train[e][3][j][0] = 1
        else:
            pass    

SyntaxError: EOF while scanning triple-quoted string literal (<ipython-input-21-1e7e3f141613>, line 103)

In [22]:
#https://www.sigmaaldrich.com/JP/ja/technical-documents/technical-article/protein-biology/protein-structural-analysis/amino-acid-reference-chart
df_aap = pd.read_table('../amino_acids_properties/amino_acid_info_merck.tsv', index_col=0)
print(df_aap)

                  3Letter 1Letter  MolecularWeight MolecularFormula  \
name                                                                  
Alanine               Ala       A            89.10          C3H7NO2   
Arginine              Arg       R           174.20        C6H14N4O2   
Asparagine            Asn       N           132.12         C4H8N2O3   
Aspartic acid         Asp       D           133.11          C4H7NO4   
Cysteine              Cys       C           121.16         C3H7NO2S   
Glutamic acid         Glu       E           147.13          C5H9NO4   
Glutamine             Gln       Q           146.15        C5H10N2O3   
Glycine               Gly       G            75.07          C2H5NO2   
Histidine             His       H           155.16         C6H9N3O2   
Hydroxyproline        Hyp       O           131.13          C5H9NO3   
Isoleucine            Ile       I           131.18         C6H13NO2   
Leucine               Leu       L           131.18         C6H13NO2   
Lysine

In [23]:
def aa_properties(e, cleave_pattern):
    for j in range(8):
        one_char_aa = cleave_pattern[j]
        if one_char_aa == "A":
            x_train[e][4][j][0] = df_aap.at['Alanine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Alanine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Alanine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Alanine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Alanine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Alanine', 'C']
            x_train[e][10][j][0] = df_aap.at['Alanine', 'H']
            x_train[e][11][j][0] = df_aap.at['Alanine', 'N']
            x_train[e][12][j][0] = df_aap.at['Alanine', 'O']
            x_train[e][13][j][0] = df_aap.at['Alanine', 'S']
        elif one_char_aa == "C":
            #x_train[e][12][j][0][2] = hydrophobicity["C"]
            x_train[e][4][j][0] = df_aap.at['Cysteine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Cysteine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Cysteine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Cysteine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Cysteine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Cysteine', 'C']
            x_train[e][10][j][0] = df_aap.at['Cysteine', 'H']
            x_train[e][11][j][0] = df_aap.at['Cysteine', 'N']
            x_train[e][12][j][0] = df_aap.at['Cysteine', 'O']
            x_train[e][13][j][0] = df_aap.at['Cysteine', 'S']
        elif one_char_aa == "D":
            #x_train[e][15][j][0][2] = hydrophobicity["D"]
            x_train[e][4][j][0] = df_aap.at['Aspartic acid', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Aspartic acid', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Aspartic acid', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Aspartic acid', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Aspartic acid', 'pl']
            x_train[e][9][j][0] = df_aap.at['Aspartic acid', 'C']
            x_train[e][10][j][0] = df_aap.at['Aspartic acid', 'H']
            x_train[e][11][j][0] = df_aap.at['Aspartic acid', 'N']
            x_train[e][12][j][0] = df_aap.at['Aspartic acid', 'O']
            x_train[e][13][j][0] = df_aap.at['Aspartic acid', 'S']
        elif one_char_aa == "E":
            #x_train[e][16][j][0][2] = hydrophobicity["E"]
            x_train[e][4][j][0] = df_aap.at['Glutamic acid', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Glutamic acid', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Glutamic acid', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Glutamic acid', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Glutamic acid', 'pl']
            x_train[e][9][j][0] = df_aap.at['Glutamic acid', 'C']
            x_train[e][10][j][0] = df_aap.at['Glutamic acid', 'H']
            x_train[e][11][j][0] = df_aap.at['Glutamic acid', 'N']
            x_train[e][12][j][0] = df_aap.at['Glutamic acid', 'O']
            x_train[e][13][j][0] = df_aap.at['Glutamic acid', 'S']
        elif one_char_aa == "F":
            #x_train[e][7][j][0][2] = hydrophobicity["F"]
            x_train[e][4][j][0] = df_aap.at['Phenylalanine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Phenylalanine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Phenylalanine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Phenylalanine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Phenylalanine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Phenylalanine', 'C']
            x_train[e][10][j][0] = df_aap.at['Phenylalanine', 'H']
            x_train[e][11][j][0] = df_aap.at['Phenylalanine', 'N']
            x_train[e][12][j][0] = df_aap.at['Phenylalanine', 'O']
            x_train[e][13][j][0] = df_aap.at['Phenylalanine', 'S']
        elif one_char_aa == "G":
            #x_train[e][0][j][0][2] = hydrophobicity["G"]
            x_train[e][4][j][0] = df_aap.at['Glycine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Glycine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Glycine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Glycine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Glycine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Glycine', 'C']
            x_train[e][10][j][0] = df_aap.at['Glycine', 'H']
            x_train[e][11][j][0] = df_aap.at['Glycine', 'N']
            x_train[e][12][j][0] = df_aap.at['Glycine', 'O']
            x_train[e][13][j][0] = df_aap.at['Glycine', 'S']
        elif one_char_aa == "H":
            #x_train[e][19][j][0][2] = hydrophobicity["H"]
            x_train[e][4][j][0] = df_aap.at['Histidine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Histidine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Histidine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Histidine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Histidine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Histidine', 'C']
            x_train[e][10][j][0] = df_aap.at['Histidine', 'H']
            x_train[e][11][j][0] = df_aap.at['Histidine', 'N']
            x_train[e][12][j][0] = df_aap.at['Histidine', 'O']
            x_train[e][13][j][0] = df_aap.at['Histidine', 'S']
        elif one_char_aa == "I":
            #x_train[e][5][j][0][2] = hydrophobicity["I"]
            x_train[e][4][j][0] = df_aap.at['Isoleucine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Isoleucine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Isoleucine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Isoleucine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Isoleucine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Isoleucine', 'C']
            x_train[e][10][j][0] = df_aap.at['Isoleucine', 'H']
            x_train[e][11][j][0] = df_aap.at['Isoleucine', 'N']
            x_train[e][12][j][0] = df_aap.at['Isoleucine', 'O']
            x_train[e][13][j][0] = df_aap.at['Isoleucine', 'S']
        elif one_char_aa == "K":
            #x_train[e][17][j][0][2] = hydrophobicity["K"]
            x_train[e][4][j][0] = df_aap.at['Lysine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Lysine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Lysine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Lysine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Lysine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Lysine', 'C']
            x_train[e][10][j][0] = df_aap.at['Lysine', 'H']
            x_train[e][11][j][0] = df_aap.at['Lysine', 'N']
            x_train[e][12][j][0] = df_aap.at['Lysine', 'O']
            x_train[e][13][j][0] = df_aap.at['Lysine', 'S']
        elif one_char_aa == "L":
            #x_train[e][4][j][0][2] = hydrophobicity["L"]
            x_train[e][4][j][0] = df_aap.at['Leucine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Leucine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Leucine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Leucine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Leucine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Leucine', 'C']
            x_train[e][10][j][0] = df_aap.at['Leucine', 'H']
            x_train[e][11][j][0] = df_aap.at['Leucine', 'N']
            x_train[e][12][j][0] = df_aap.at['Leucine', 'O']
            x_train[e][13][j][0] = df_aap.at['Leucine', 'S']
        elif one_char_aa == "M":
            #x_train[e][6][j][0][2] = hydrophobicity["M"]
            x_train[e][4][j][0] = df_aap.at['Methionine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Methionine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Methionine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Methionine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Methionine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Methionine', 'C']
            x_train[e][10][j][0] = df_aap.at['Methionine', 'H']
            x_train[e][11][j][0] = df_aap.at['Methionine', 'N']
            x_train[e][12][j][0] = df_aap.at['Methionine', 'O']
            x_train[e][13][j][0] = df_aap.at['Methionine', 'S']
        elif one_char_aa == "N":
            #x_train[e][13][j][0][2] = hydrophobicity["N"]
            x_train[e][4][j][0] = df_aap.at['Asparagine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Asparagine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Asparagine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Asparagine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Asparagine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Asparagine', 'C']
            x_train[e][10][j][0] = df_aap.at['Asparagine', 'H']
            x_train[e][11][j][0] = df_aap.at['Asparagine', 'N']
            x_train[e][12][j][0] = df_aap.at['Asparagine', 'O']
            x_train[e][13][j][0] = df_aap.at['Asparagine', 'S']
        elif one_char_aa == "P":
            #x_train[e][1][j][0][2] = hydrophobicity["P"]
            x_train[e][4][j][0] = df_aap.at['Proline', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Proline', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Proline', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Proline', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Proline', 'pl']
            x_train[e][9][j][0] = df_aap.at['Proline', 'C']
            x_train[e][10][j][0] = df_aap.at['Proline', 'H']
            x_train[e][11][j][0] = df_aap.at['Proline', 'N']
            x_train[e][12][j][0] = df_aap.at['Proline', 'O']
            x_train[e][13][j][0] = df_aap.at['Proline', 'S']
        elif one_char_aa == "Q":
            #x_train[e][14][j][0][2] = hydrophobicity["Q"]
            x_train[e][4][j][0] = df_aap.at['Glutamine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Glutamine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Glutamine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Glutamine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Glutamine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Glutamine', 'C']
            x_train[e][10][j][0] = df_aap.at['Glutamine', 'H']
            x_train[e][11][j][0] = df_aap.at['Glutamine', 'N']
            x_train[e][12][j][0] = df_aap.at['Glutamine', 'O']
            x_train[e][13][j][0] = df_aap.at['Glutamine', 'S']
        elif one_char_aa == "R":
            #x_train[e][18][j][0][2] = hydrophobicity["R"]
            x_train[e][4][j][0] = df_aap.at['Arginine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Arginine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Arginine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Arginine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Arginine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Arginine', 'C']
            x_train[e][10][j][0] = df_aap.at['Arginine', 'H']
            x_train[e][11][j][0] = df_aap.at['Arginine', 'N']
            x_train[e][12][j][0] = df_aap.at['Arginine', 'O']
            x_train[e][13][j][0] = df_aap.at['Arginine', 'S']
        elif one_char_aa == "S":
            #x_train[e][10][j][0][2] = hydrophobicity["S"]
            x_train[e][4][j][0] = df_aap.at['Serine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Serine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Serine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Serine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Serine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Serine', 'C']
            x_train[e][10][j][0] = df_aap.at['Serine', 'H']
            x_train[e][11][j][0] = df_aap.at['Serine', 'N']
            x_train[e][12][j][0] = df_aap.at['Serine', 'O']
            x_train[e][13][j][0] = df_aap.at['Serine', 'S']
        elif one_char_aa == "T":
            #x_train[e][11][j][0][2] = hydrophobicity["T"]
            x_train[e][4][j][0] = df_aap.at['Threonine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Threonine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Threonine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Threonine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Threonine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Threonine', 'C']
            x_train[e][10][j][0] = df_aap.at['Threonine', 'H']
            x_train[e][11][j][0] = df_aap.at['Threonine', 'N']
            x_train[e][12][j][0] = df_aap.at['Threonine', 'O']
            x_train[e][13][j][0] = df_aap.at['Threonine', 'S']
        elif one_char_aa == "V":
            #x_train[e][3][j][0][2] = hydrophobicity["V"]
            x_train[e][4][j][0] = df_aap.at['Valine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Valine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Valine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Valine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Valine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Valine', 'C']
            x_train[e][10][j][0] = df_aap.at['Valine', 'H']
            x_train[e][11][j][0] = df_aap.at['Valine', 'N']
            x_train[e][12][j][0] = df_aap.at['Valine', 'O']
            x_train[e][13][j][0] = df_aap.at['Valine', 'S']
        elif one_char_aa == "W":
            #x_train[e][9][j][0][2] = hydrophobicity["W"]
            x_train[e][4][j][0] = df_aap.at['Tryptophan', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Tryptophan', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Tryptophan', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Tryptophan', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Tryptophan', 'pl']
            x_train[e][9][j][0] = df_aap.at['Tryptophan', 'C']
            x_train[e][10][j][0] = df_aap.at['Tryptophan', 'H']
            x_train[e][11][j][0] = df_aap.at['Tryptophan', 'N']
            x_train[e][12][j][0] = df_aap.at['Tryptophan', 'O']
            x_train[e][13][j][0] = df_aap.at['Tryptophan', 'S']
        elif one_char_aa == "Y":
            #x_train[e][8][j][0][2] = hydrophobicity["Y"]
            x_train[e][4][j][0] = df_aap.at['Tyrosine', 'MolecularWeight']
            x_train[e][5][j][0] = df_aap.at['Tyrosine', 'ResidueWeight_without_water']
            x_train[e][6][j][0] = df_aap.at['Tyrosine', 'pKa']
            x_train[e][7][j][0] = df_aap.at['Tyrosine', 'pKb']
            x_train[e][8][j][0] = df_aap.at['Tyrosine', 'pl']
            x_train[e][9][j][0] = df_aap.at['Tyrosine', 'C']
            x_train[e][10][j][0] = df_aap.at['Tyrosine', 'H']
            x_train[e][11][j][0] = df_aap.at['Tyrosine', 'N']
            x_train[e][12][j][0] = df_aap.at['Tyrosine', 'O']
            x_train[e][13][j][0] = df_aap.at['Tyrosine', 'S']
        else:
            pass    

In [24]:
def get_uid(m):
    for j in range(4):
        if re.match(r'^[A-Z]{1}[0-9A-Z]{5}$', str(df.iloc[i+m, j])):
            result = re.match(r'^[A-Z]{1}[0-9A-Z]{5}$', str(df.iloc[i+m, j]))
            uniprot_id = result.group(0)
            print(f'uniprot_id: {uniprot_id}')
            break
        else:
            uniprot_id = "null"
            print(f'uniprot_id: null')
    return uniprot_id

### main()処理

In [25]:
# 各アミノ酸について電荷と疎水性の値を定義
charge = {"A":0., "C":-0.0735876, "D":-0.9994991, "E":-0.9987427, "F":0., "G":0., "H":0.0593509, "I":0.,
          "K":0.9997489, "L":0., "M":0., "N":0., "P":0., "Q":0., "R":0.9999950, "S":0., "T":0., "V":0., "W":0., "Y":-0.0001995}
hydrophobicity = {"A":0.1630295, "C":-0.2554557, "D":-0.9794608, "E":-0.7458280, "F":0.9152760,
                  "G":-0.2554557, "H":-0.7869063, "I":0.8510911, "K":-0.8510911, "L":1.,
                  "M":0.7227214, "N":-1., "P":-0.0860077, "Q":-0.8305520, "R":-0.7021823,
                  "S":-0.4685494, "T":-0.3838254, "V":0.6816431, "W":0.8305520, "Y":0.5738126}

In [26]:
#new cell
#2.1
#define ""negative"" data array 

#3

count = 0
protease_turn = 0
#index = 0
consecutive_uid = 0
uid_list = []
flag = 0
check = 0
total_subs_count = 0
subs_sum = 0

eight_aa_list = []
#skipp = 0
negative_data_dict = {}

for key_name in positive_proteases_txt:
    filename = positive_proteases_txt[key_name]
    path = f'../trainingdata(positive)/{filename}'
    df = pd.read_csv(path, sep='\t')
    display(df)
    
    print("==================================protease"+str(count)+"=======================================")
    x_train = np.zeros([len(df), 14, 8, 1])
    #print(x_train)
    print("len(x_train):"+str(len(x_train)))
        
    skipp = 0
    for i in range(len(df)):
        uid=""
        cleave_point_set = []
        flag = 0
        total_subs_count = total_subs_count + 1
        print("total_subs_count: "+str(total_subs_count))
        
        df_negative_pattern=pd.DataFrame(
            data={'uniprot_id':[], 'negative_pattern':[]}
        )

        if skipp > 0:
            print("This row was skipped.")
            skipp = skipp - 1
            continue


        print("-------------------------------protease "+str(protease_turn)+"substrate "+str(i)+"-------------------------------------")
        #get the position of p4 column
        for j in range(5):
            #print(f'j: {j}')
            if re.match(r'^(N)*(S)*(P)*$', str(df.iloc[i, j])):
                p4_column = j + 2
                print(f'p4_column: {p4_column}')
                break
        #func1
        cleave_pattern = ""
        cleave_pattern = get_cleave_pattern(p4_column)    
        #print(f'cleave_pattern: {cleave_pattern}')


        #uidを抽出
        uid = get_uid(0)
        print(f'uid: {uid}')
        if uid == "null":
            print("This data does not have Uniprot ID, so this substrate cannot create an negative data.")
            continue
        uid_list = []
        uid = str(uid)
        uid_list.append(uid)
        print(f'uid_list: {uid_list}')

        fullaa = aaseq_from_uid(uid, protease_turn, i)
        print("fullaa_len: "+str(len(fullaa)))
        if len(fullaa) < 16:
            continue
        #index = index + 1
        
        m = 1

        while 1:
            if i+m == len(df):
                break

            #print(uid_list)
            print("below id is next_uid.")
            next_uid = get_uid(m)

            if next_uid == uid:
                print("next_uid is same with start uid.")
                uid_list.append(next_uid)
                p4, cleave_point_lists = get_cleave_point(fullaa, cleave_pattern)
                cleave_point_set = cleave_point_set + cleave_point_lists
                #print(cleave_point_set)
                
                #eight_aa, p4, cleave_point_list = get_negative_data_seq(fullaa, cleave_pattern)
                #eight_aa_list = eight_aa_list + eight_aa
                print(f'cleave_point_set: {cleave_point_set}')
                consecutive_uid = consecutive_uid + 1
                print(f'uid_list: {uid_list}')
                
            elif next_uid == "null":
                skipp = len(uid_list) - 1
                print(f'uid_list!: {uid_list}')
                print("uid_list_len: "+str(len(uid_list)))
                break                    
            else:
                skipp = len(uid_list) - 1
                print(f'uid_list: {uid_list}')
                print("uid_list_len: "+str(len(uid_list)))
                break
            m = m + 1
            print(m)  
            
        if m == 1:
            p4, cleave_point_set = get_cleave_point(fullaa, cleave_pattern)

        if p4 == -1:
            continue

        e = i
        negative_eight_aa_set = get_negative_data_seq(fullaa, cleave_point_set)
        print(negative_eight_aa_set)
        print(f'len(negative_eight_aa_set): {len(negative_eight_aa_set)}')
        for h in range(len(negative_eight_aa_set)):
            eight_aa = negative_eight_aa_set[h]
            #func2
            #aa_onezero(eight_aa)

            #func3
            aa_charge(e, eight_aa)     

            #func4
            aa_hypho(e, eight_aa)         

            #func5
            #p4 = cleave_point
            secondary_str = add_secondary_structure(e, uid, p4, eight_aa)
            if secondary_str == 0:
                secondary_structure = "null"
            else:
                secondary_structure = "not_null"

            #func6
            aa_properties(e, eight_aa)       

            df_negative_pattern.loc[f'{e}'] = [uid, eight_aa]
            display(df_negative_pattern)
            negative_data_dict[check] = [str(total_subs_count), str(protease_turn), uid, cleave_pattern, eight_aa, secondary_structure, x_train[e]]            
 
            check = check + 1
            print("check: "+str(check))
            print("total_subs_count: "+str(total_subs_count))
            e = e + 1           
    filename = f'../trainingdata(positive)/v8-16/cleave_pattern_one_letter_aa_{key_name}_negative_data.csv'
    df_negative_pattern.to_csv(filename)
    
    protease_turn = protease_turn + 1
    print("The number of substrates that had multiple same cleavage sites: "+str(flag))
    np.save('../saving_numpy_array/v8-16/x_train/x_train_negative_v8-16_protease'+str(protease_turn), x_train)
        
    print("count")
    print(count)
    if count == 0:
        x_train_negative_all = x_train
    else:
        x_train_negative_all = np.append(x_train_negative_all, x_train, 0)
    subs_sum = subs_sum + len(df)
    count = count + 1
    
print("consecutive_uid: "+str(consecutive_uid))
print("subs_sum: "+str(subs_sum))
print("total_subs_count: "+str(total_subs_count))

print("END")

Substrate  Uniprot  \
0                                              P78365  109-134   
1                                              Q6ZS99  285-301   
2   116 kDa U5 small nuclear ribonucleoprotein com...   Q15029   
3                                14-3-3 protein theta   P27348   
4                           40S ribosomal protein S12   P25398   
..                                                ...      ...   
95   Urokinase plasminogen activator surface receptor   Q03405   
96                                           Vimentin   Q8N850   
97                                           Vinculin   P18206   
98  von Willebrand factor A domain-containing prot...   Q5TIE3   
99  Zinc finger Ran-binding domain-containing prot...   O95218   

                 Residue range               Cleavage Site Cleavage type  \
0   peptide-Ser123+Ser-peptide                           N            MS   
1           AR+TLLAKNLPYKVTQDE                           N            MS   
2                      487-512  peptide-Arg495+Val-peptide             N   
3                      138-151             R+KQTIDNSQGAYQE             N   
4                       98-117       GKPR+KVVGCSCVVVKDYGKE             N   
..                         ...                         ...           ...   
95                      23-305  peptide-Arg111+Ser-peptide             P   
96                     157-172           LR+RQVDQLTNDKARVE             N   
97                     820-833             SGYR+ILGAVAKVRE             N   
98                    990-1007         GPQRSLATNT+LSSMKASE             N   
99                     127-147      FGRKKKKYR+GKAVGPASILKE             N   

   Evidence   P4   P3   P2   P1  P1'  P2'  P3'                 P4'  \
0       Asn  Ser  Ala  Ser  Ser  Ile  Ala  Gly  Barr� et al., 2014   
1         -    -  Ala  Arg  Thr  Leu  Leu  Ala  Barr� et al., 2014   
2        MS  Ala  Phe  Gly  Arg  Val  Leu  Ser                 Gly   
3        MS    -    -    -  Arg  Lys  Gln  Thr                 Ile   
4        MS  Gly  Lys  Pro  Arg  Lys  Val  Val                 Gly   
..      ...  ...  ...  ...  ...  ...  ...  ...                 ...   
95       NT  Thr  Tyr  Ser  Arg  Ser  Arg  Tyr                 Leu   
96       MS    -    -  Leu  Arg  Arg  Gln  Val                 Asp   
97       MS  Ser  Gly  Tyr  Arg  Ile  Leu  Gly                 Ala   
98       MS  Ala  Thr  Asn  Thr  Leu  Ser  Ser                 Met   
99       MS  Lys  Lys  Tyr  Arg  Gly  Lys  Ala                 Val   

                Reference  CutDB  MERNUM  
0                     NaN    NaN     NaN  
1                     NaN    NaN     NaN  
2      Barr� et al., 2014    NaN     NaN  
3      Barr� et al., 2014    NaN     NaN  
4      Barr� et al., 2014    NaN     NaN  
..                    ...    ...     ...  
95  Beaufort et al., 2007    NaN     NaN  
96     Barr� et al., 2014    NaN     NaN  
97     Barr� et al., 2014    NaN     NaN  
98     Barr� et al., 2014    NaN     NaN  
99     Barr� et al., 2014    NaN     NaN  

[100 rows x 17 columns]

==================================protease0=======================================
len(x_train):100
total_subs_count: 1
-------------------------------protease 0substrate 0-------------------------------------
p4_column: 5
three_aa: Asn
one_aa: N
three_aa: Ser
one_aa: S
three_aa: Ala
one_aa: A
three_aa: Ser
one_aa: S
three_aa: Ser
one_aa: S
three_aa: Ile
one_aa: I
three_aa: Ala
one_aa: A
three_aa: Gly
one_aa: G
cleave_pattern: NSASSIAG
uniprot_id: P78365
uid: P78365
uid_list: ['P78365']
function was not detected.


uniprotKB_accession function  \
protease0_substrate0              P78365        1   

                                                               sequence  
protease0_substrate0  MCLRGGCSPRAPAAAPQPRPPPALPPRPRAPVPASRPGRPLLTPAR...

fullaa_len: 433
below id is next_uid.
uniprot_id: Q6ZS99
uid_list: ['P78365']
uid_list_len: 1
NSASSIAG
NSASSIAG
[119]
cleave_point: 119
cleave_point_list: [119]
[112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126]
[229 159  54 208  10 272 175 255 284 424  21 407 122 194 249 259 352 218
 316 331 344 190 378   1  37 134  65 158 307  12 303 382 179 318 274 154
  96 315 345 217 384 153 358 388  15 278  60 332 418 113 356 367   6  90
 150 421 102  76 220 145 198  59 261 364 410 308  78 325 141 385 155 160
 107 176 340 124  49  52  74  26  45 144   4 224 213 100 254 312 389   5
 171 317 395   7 199  22  68 311  20 135 271  14 371 301 219 247 142  75
  64  55  81 347 360 413  71 397 401 225 404 383 191 157  56   8 236 164
 132 188 238 282 106 268  63 293 363 372 417  89 245 200 346 281  92 252
 348 186 168 240  66 263 327 140 101 398 310 349  17 146 276 206  30 114
 170 103 205 264 196 116 353 120 233 112 366 136 296 126 373 320 302 133
  33 402 162  34 241  97  85  61 

uniprot_id negative_pattern
0     P78365         KFKRSKRF

...

check: 193
total_subs_count: 228
total_subs_count: 229
-------------------------------protease 3substrate 9-------------------------------------
p4_column: 6
three_aa: Leu
one_aa: L
three_aa: Asn
one_aa: N
three_aa: Gln
one_aa: Q
three_aa: Arg
one_aa: R
three_aa: Ser
one_aa: S
three_aa: Ile
one_aa: I
three_aa: Met
one_aa: M
three_aa: Glu
one_aa: E
cleave_pattern: LNQRSIME
uniprot_id: null
uniprot_id: P37091
uid: P37091
uid_list: ['P37091']


uniprotKB_accession  \
protease3_substrate9              P37091   

                                                               function  \
protease3_substrate9  Sodium permeable non-voltage-sensitive ion cha...   

                                                               sequence  
protease3_substrate9  MAPGEKIKAKIKKNLPVRGPQAPTIKDLMHWYCMNTNTHGCRRIVV...

fullaa_len: 650
LNQRSIME
LNQRSIME
[511]
cleave_point: 511
cleave_point_list: [511]
[504, 505, 506, 507, 508, 509, 510, 511, 512, 513, 514, 515, 516, 517, 518]
[122 155 498 103 594 222 231 463 196 524 332 574 481 336 494 362 435 343
 571 194 491 379 525 334 157 213 441 485 101  55  85 456  48 415 493 501
 298 187 200 558 589 631 557 271 245  50 278 378 639  14  52 611 420 641
  49 236 489 624 352 230 539  75  17 162 235 233 406 433 202 597 173 367
 495 409 144 283  62 272 266 633 294 318   1 522 607 354 547  45 578 395
   8 443 635  31  21  77 436 211 508 170 240 127 165 523 142 519 634 483
 178 317  37 514 330 224 492  34 419 598  64 640 532 428 385 263  10 175
 315 190 408  12 386 573 499  78  92 391  66 261 205 588 301  15   6 621
 427 319 454 503 229 581 333 384 304  90 575 390 118 618 440 521 478 193
 636 268 526 609 247 561 471 344 132 592 299 172  97 622 562 452 252  96
 338 566 242  89 392 474 462 517  46 239 446 531 397 303 107 249 417   0
 246  71 206 102 511 108 400 210 584 3

uniprot_id negative_pattern
9     P37091         QALLSLYG

check: 194
total_subs_count: 229
The number of substrates that had multiple same cleavage sites: 0
count
3
consecutive_uid: 26
subs_sum: 229
total_subs_count: 229
END


In [63]:
negative_data_dict

{0: [1,
  0,
  'P78365',
  'NSASSIAG',
  'null',
  array([[[  0.9997489],
          [  0.       ],
          [  0.9997489],
          [  0.999995 ],
          [  0.       ],
          [  0.9997489],
          [  0.999995 ],
          [  0.       ]],
  
         [[ -0.8510911],
          [  0.915276 ],
          [ -0.8510911],
          [ -0.7021823],
          [ -0.4685494],
          [ -0.8510911],
          [ -0.7021823],
          [  0.915276 ]],
  
         [[  0.       ],
          [  0.       ],
          [  0.       ],
          [  0.       ],
          [  0.       ],
          [  0.       ],
          [  0.       ],
          [  0.       ]],
  
         [[  0.       ],
          [  0.       ],
          [  0.       ],
          [  0.       ],
          [  0.       ],
          [  0.       ],
          [  0.       ],
          [  0.       ]],
  
         [[146.19     ],
          [165.19     ],
          [146.19     ],
          [174.2      ],
          [105.09     ],
          

In [ ]:
import pickle

#my_dict = { 'Apple': 4, 'Banana': 2, 'Orange': 6, 'Grapes': 11}

with open("../saving_numpy_array/v8-16/x_train/all/negative_data_dic_v8-16.pkl", "wb") as tf:
    pickle.dump(negative_data_dict,tf)

In [ ]:
import pickle

with open("../saving_numpy_array/v8-16/x_train/all/negative_data_dic_v8-16.pkl" "wb") as tf:
    data = pickle.load(tf)

print(data.item())

In [62]:
len(negative_data_dic)

194

In [ ]:
'''
import json

my_dict = { 'Apple': 4, 'Banana': 2, 'Orange': 6, 'Grapes': 11}

tf = open("myDictionary.json", "w")
json.dump(my_dict,tf)
tf.close()

In [71]:
#import json 

In [72]:
#tf = open("../saving_numpy_array/v8-16/x_train/all/negative_data_dic.json", "w")
#json.dump(negative_data_dic,tf)
#tf.close()

TypeError: Object of type ndarray is not JSON serializable

In [ ]:
'''
import numpy as np

my_dict = { 'Apple': 4, 'Banana': 2, 'Orange': 6, 'Grapes': 11}
np.save('file.npy', my_dict)

In [73]:
np.save("../saving_numpy_array/v8-16/x_train/all/negative_data_dic.npy", negative_data_dic)

In [74]:
new_dict = np.load("../saving_numpy_array/v8-16/x_train/all/negative_data_dic.npy", allow_pickle='TRUE')
print(new_dict)

{0: [1, 0, 'P78365', 'NSASSIAG', 'null', array([[[  0.9997489],
        [  0.       ],
        [  0.9997489],
        [  0.999995 ],
        [  0.       ],
        [  0.9997489],
        [  0.999995 ],
        [  0.       ]],

       [[ -0.8510911],
        [  0.915276 ],
        [ -0.8510911],
        [ -0.7021823],
        [ -0.4685494],
        [ -0.8510911],
        [ -0.7021823],
        [  0.915276 ]],

       [[  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ]],

       [[  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ]],

       [[146.19     ],
        [165.19     ],
        [146.19     ],
        [174.2      ],
        [105.09     ],
        [146.19     ],
        [174.2      ],
        [165.19     ]],

       [[128.18     ],
      

In [76]:
len(new_dict)

TypeError: len() of unsized object

In [81]:
new_dict

IndexError: too many indices for array

In [77]:
len(negative_data_dic)

194

In [ ]:
'''
import json

tf = open("myDictionary.json", "r")
new_dict = json.load(tf)
print(new_dict)

ここの計算は6分あれば終わる．

## save negative

In [82]:
#save negative
np.save('../saving_numpy_array/v8-16/x_train/all/x_train_all_v8-16_only_negative', x_train_negative_all)

## load negative, if you need.

In [7]:
#load negative, if you need.
x_train_negative_all = np.load('../saving_numpy_array/v8-16/x_train/all/x_train_all_v8-16_only_negative.npy')

In [ ]:
#x_train_all = x_train_positive_all

In [83]:
print(len(x_train_positive_all))
print(len(x_train_negative_all))
print(len(x_train_positive_all_5crossval))

print(len(y_train_positive_all))
print(len(y_train_positive_all_5crossval))
print(subs_sum)

166
189
41
166
41
229


## データを代入しなかったスパース行列を数えて，削除する．

In [84]:
#スパース行列を数える．
del_list = []
for i in range(len(x_train_negative_all)):
    #print(x_train_all[i])
    a = x_train_negative_all[i]
    #print(a)
    
    zero_row_count = 0
    for j in range(14):
        print(a[j])
        if np.all(a[j]==0):
            zero_row_count = zero_row_count + 1
    if zero_row_count == 14:
        del_list.append(i)
    print("=====================================================")
    

#x_train_all = np.delete(x_train_all, del_list, 0)
print(x_train_negative_all)
print(len(x_train_negative_all))
print(len(del_list))
    
#https://engineeeer.com/check-numpy-array-all-zero/

[[0.9997489]
 [0.       ]
 [0.9997489]
 [0.999995 ]
 [0.       ]
 [0.9997489]
 [0.999995 ]
 [0.       ]]
[[-0.8510911]
 [ 0.915276 ]
 [-0.8510911]
 [-0.7021823]
 [-0.4685494]
 [-0.8510911]
 [-0.7021823]
 [ 0.915276 ]]
[[0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]]
[[0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]]
[[146.19]
 [165.19]
 [146.19]
 [174.2 ]
 [105.09]
 [146.19]
 [174.2 ]
 [165.19]]
[[128.18]
 [147.18]
 [128.18]
 [156.19]
 [ 87.08]
 [128.18]
 [156.19]
 [147.18]]
[[2.18]
 [1.83]
 [2.18]
 [2.17]
 [2.21]
 [2.18]
 [2.17]
 [1.83]]
[[8.95]
 [9.13]
 [8.95]
 [9.04]
 [9.15]
 [8.95]
 [9.04]
 [9.13]]
[[ 9.74]
 [ 5.48]
 [ 9.74]
 [10.76]
 [ 5.68]
 [ 9.74]
 [10.76]
 [ 5.48]]
[[6.]
 [9.]
 [6.]
 [6.]
 [3.]
 [6.]
 [6.]
 [9.]]
[[14.]
 [11.]
 [14.]
 [14.]
 [ 7.]
 [14.]
 [14.]
 [11.]]
[[2.]
 [1.]
 [2.]
 [4.]
 [1.]
 [2.]
 [4.]
 [1.]]
[[2.]
 [2.]
 [2.]
 [2.]
 [3.]
 [2.]
 [2.]
 [2.]]
[[0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]]
[[ 9.997489e-01]
 [ 0.000000e+00]
 [ 0.000000e+00]
 [-1.995000e-04

In [85]:
#スパース行列を削除する．
del_list = []
for i in range(len(x_train_negative_all)):
    #print(x_train_all[i])
    a = x_train_negative_all[i]
    #print(a)
    
    zero_row_count = 0
    for j in range(14):
        print(a[j])
        if np.all(a[j]==0):
            zero_row_count = zero_row_count + 1
    if zero_row_count == 14:
        del_list.append(i)
    print("=====================================================")
    

x_train_negative_all = np.delete(x_train_negative_all, del_list, 0)
print(x_train_negative_all)
print(len(x_train_negative_all))
print(len(del_list))

#https://engineeeer.com/check-numpy-array-all-zero/

[[0.9997489]
 [0.       ]
 [0.9997489]
 [0.999995 ]
 [0.       ]
 [0.9997489]
 [0.999995 ]
 [0.       ]]
[[-0.8510911]
 [ 0.915276 ]
 [-0.8510911]
 [-0.7021823]
 [-0.4685494]
 [-0.8510911]
 [-0.7021823]
 [ 0.915276 ]]
[[0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]]
[[0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]]
[[146.19]
 [165.19]
 [146.19]
 [174.2 ]
 [105.09]
 [146.19]
 [174.2 ]
 [165.19]]
[[128.18]
 [147.18]
 [128.18]
 [156.19]
 [ 87.08]
 [128.18]
 [156.19]
 [147.18]]
[[2.18]
 [1.83]
 [2.18]
 [2.17]
 [2.21]
 [2.18]
 [2.17]
 [1.83]]
[[8.95]
 [9.13]
 [8.95]
 [9.04]
 [9.15]
 [8.95]
 [9.04]
 [9.13]]
[[ 9.74]
 [ 5.48]
 [ 9.74]
 [10.76]
 [ 5.68]
 [ 9.74]
 [10.76]
 [ 5.48]]
[[6.]
 [9.]
 [6.]
 [6.]
 [3.]
 [6.]
 [6.]
 [9.]]
[[14.]
 [11.]
 [14.]
 [14.]
 [ 7.]
 [14.]
 [14.]
 [11.]]
[[2.]
 [1.]
 [2.]
 [4.]
 [1.]
 [2.]
 [4.]
 [1.]]
[[2.]
 [2.]
 [2.]
 [2.]
 [3.]
 [2.]
 [2.]
 [2.]]
[[0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]
 [0.]]
[[ 9.997489e-01]
 [ 0.000000e+00]
 [ 0.000000e+00]
 [-1.995000e-04

In [69]:
print(len(x_train_negative_all))

189


In [19]:
print(x_train_negative_all[0])

[[[  0.9997489]
  [  0.       ]
  [  0.9997489]
  [  0.999995 ]
  [  0.       ]
  [  0.9997489]
  [  0.999995 ]
  [  0.       ]]

 [[ -0.8510911]
  [  0.915276 ]
  [ -0.8510911]
  [ -0.7021823]
  [ -0.4685494]
  [ -0.8510911]
  [ -0.7021823]
  [  0.915276 ]]

 [[  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]]

 [[  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]]

 [[146.19     ]
  [165.19     ]
  [146.19     ]
  [174.2      ]
  [105.09     ]
  [146.19     ]
  [174.2      ]
  [165.19     ]]

 [[128.18     ]
  [147.18     ]
  [128.18     ]
  [156.19     ]
  [ 87.08     ]
  [128.18     ]
  [156.19     ]
  [147.18     ]]

 [[  2.18     ]
  [  1.83     ]
  [  2.18     ]
  [  2.17     ]
  [  2.21     ]
  [  2.18     ]
  [  2.17     ]
  [  1.83     ]]

 [[  8.95     ]
  [  9.13     ]
  [  8.95     ]
  [  9.04     ]
  [  9.15     ]
  [  8.95 

In [86]:
five_cross = len(x_train_negative_all)//5
print(five_cross)

37


In [88]:
five_cross = len(negative_data_dic)//5
print(five_cross)

38


In [13]:
#print(five_cross)

37


In [89]:
rand_list_5cross = random.sample(range(0, len(negative_data_dic), 1), k=five_cross)

In [90]:
print(rand_list_5cross)

[109, 153, 17, 40, 27, 96, 115, 163, 1, 130, 67, 147, 68, 4, 81, 58, 121, 97, 55, 142, 175, 31, 181, 65, 119, 33, 13, 92, 185, 182, 80, 172, 61, 148, 29, 22, 23, 106]


In [91]:
df1 = pd.DataFrame(
    data={'check': rand_list_5cross}
)
 
df1

check
0     109
1     153
2      17
3      40
4      27
5      96
6     115
7     163
8       1
9     130
10     67
11    147
12     68
13      4
14     81
15     58
16    121
17     97
18     55
19    142
20    175
21     31
22    181
23     65
24    119
25     33
26     13
27     92
28    185
29    182
30     80
31    172
32     61
33    148
34     29
35     22
36     23
37    106

In [92]:
df1.to_csv("../saving_numpy_array/v8-16/x_train/all/x_train_negative_all_5crossval_v8-16.csv")

In [93]:
print(len(rand_list_5cross))

38


# 検証データpositive_5crossvalを作る．

In [100]:
count = 0
for i in rand_list_5cross:
    if count == 0:
        x_train_negative_all_5crossval = [negative_data_dic[i][5]]
    else:
        x_train_negative_all_5crossval = np.append(x_train_negative_all_5crossval, [negative_data_dic[i][5]], 0)
    count = count + 1
    print(negative_data_dic[i])
    

[130, 1, 'P09496', 'SRMRSVLI', 'null', array([[[  0.       ],
        [  0.999995 ],
        [  0.9997489],
        [  0.       ],
        [  0.999995 ],
        [ -0.9987427],
        [ -0.9987427],
        [  0.       ]],

       [[  0.8510911],
        [ -0.7021823],
        [ -0.8510911],
        [  0.830552 ],
        [ -0.7021823],
        [ -0.745828 ],
        [ -0.745828 ],
        [ -0.830552 ]],

       [[  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ]],

       [[  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ]],

       [[131.18     ],
        [174.2      ],
        [146.19     ],
        [204.23     ],
        [174.2      ],
        [147.13     ],
        [147.13     ],
        [146.15     ]],

       [[113.16     ],
        

In [95]:
print(count)

38


In [96]:
print(len(x_train_negative_all_5crossval))

38


In [121]:
np.save('../saving_numpy_array/v8-16/x_train/all/x_train_negative_all_5crossval_v8-16', x_train_negative_all_5crossval)

In [101]:
print(x_train_negative_all_5crossval[0])

[[[  0.       ]
  [  0.999995 ]
  [  0.9997489]
  [  0.       ]
  [  0.999995 ]
  [ -0.9987427]
  [ -0.9987427]
  [  0.       ]]

 [[  0.8510911]
  [ -0.7021823]
  [ -0.8510911]
  [  0.830552 ]
  [ -0.7021823]
  [ -0.745828 ]
  [ -0.745828 ]
  [ -0.830552 ]]

 [[  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]]

 [[  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]
  [  0.       ]]

 [[131.18     ]
  [174.2      ]
  [146.19     ]
  [204.23     ]
  [174.2      ]
  [147.13     ]
  [147.13     ]
  [146.15     ]]

 [[113.16     ]
  [156.19     ]
  [128.18     ]
  [186.22     ]
  [156.19     ]
  [129.12     ]
  [129.12     ]
  [128.13     ]]

 [[  2.36     ]
  [  2.17     ]
  [  2.18     ]
  [  2.83     ]
  [  2.17     ]
  [  2.19     ]
  [  2.19     ]
  [  2.17     ]]

 [[  9.6      ]
  [  9.04     ]
  [  8.95     ]
  [  9.39     ]
  [  9.04     ]
  [  9.67 

In [103]:
negative_all_list = set(list(range(0, len(negative_data_dic)))) - set(rand_list_5cross)
print(negative_all_list)

{0, 2, 3, 5, 6, 7, 8, 9, 10, 11, 12, 14, 15, 16, 18, 19, 20, 21, 24, 25, 26, 28, 30, 32, 34, 35, 36, 37, 38, 39, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 56, 57, 59, 60, 62, 63, 64, 66, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 93, 94, 95, 98, 99, 100, 101, 102, 103, 104, 105, 107, 108, 110, 111, 112, 113, 114, 116, 117, 118, 120, 122, 123, 124, 125, 126, 127, 128, 129, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 143, 144, 145, 146, 149, 150, 151, 152, 154, 155, 156, 157, 158, 159, 160, 161, 162, 164, 165, 166, 167, 168, 169, 170, 171, 173, 174, 176, 177, 178, 179, 180, 183, 184, 186, 187, 188, 189, 190, 191, 192, 193}


In [105]:
print(len(negative_all_list))

156


In [106]:
'''
dlist1= list(range(0, len(positive_data_dic)))
dlist2 = rand_list_5cross
dlist3 = [i for i in dlist1 if i not in dlist2]
print(dlist3)
print(len(dlist3))

SyntaxError: EOF while scanning triple-quoted string literal (<ipython-input-106-9183d0275a85>, line 6)

# 訓練データnegative_allを作る．

In [107]:
count = 0
for i in negative_all_list:
    if count == 0:
        x_train_negative_all = [negative_data_dic[i][5]]
    else:
        x_train_negative_all = np.append(x_train_negative_all, [negative_data_dic[i][5]], 0)
    count = count + 1
    print(negative_data_dic[i])
    

[1, 0, 'P78365', 'NSASSIAG', 'null', array([[[  0.9997489],
        [  0.       ],
        [  0.9997489],
        [  0.999995 ],
        [  0.       ],
        [  0.9997489],
        [  0.999995 ],
        [  0.       ]],

       [[ -0.8510911],
        [  0.915276 ],
        [ -0.8510911],
        [ -0.7021823],
        [ -0.4685494],
        [ -0.8510911],
        [ -0.7021823],
        [  0.915276 ]],

       [[  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ]],

       [[  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ]],

       [[146.19     ],
        [165.19     ],
        [146.19     ],
        [174.2      ],
        [105.09     ],
        [146.19     ],
        [174.2      ],
        [165.19     ]],

       [[128.18     ],
        [1

In [108]:
x_train_negative_all

array([[[[ 9.997489e-01],
         [ 0.000000e+00],
         [ 9.997489e-01],
         ...,
         [ 9.997489e-01],
         [ 9.999950e-01],
         [ 0.000000e+00]],

        [[-8.510911e-01],
         [ 9.152760e-01],
         [-8.510911e-01],
         ...,
         [-8.510911e-01],
         [-7.021823e-01],
         [ 9.152760e-01]],

        [[ 0.000000e+00],
         [ 0.000000e+00],
         [ 0.000000e+00],
         ...,
         [ 0.000000e+00],
         [ 0.000000e+00],
         [ 0.000000e+00]],

        ...,

        [[ 2.000000e+00],
         [ 1.000000e+00],
         [ 2.000000e+00],
         ...,
         [ 2.000000e+00],
         [ 4.000000e+00],
         [ 1.000000e+00]],

        [[ 2.000000e+00],
         [ 2.000000e+00],
         [ 2.000000e+00],
         ...,
         [ 2.000000e+00],
         [ 2.000000e+00],
         [ 2.000000e+00]],

        [[ 0.000000e+00],
         [ 0.000000e+00],
         [ 0.000000e+00],
         ...,
         [ 0.000000e+00],
        

In [123]:
print(len(x_train_negative_all))

156


In [124]:
np.save('../saving_numpy_array/v8-16/x_train/all/x_train_negative_all_v8-16', x_train_negative_all)

# positive_dataとnegative_dataの結合

In [112]:
print(len(np.concatenate([x_train_positive_all, x_train_negative_all], 0)))
# [[1 1 1]
#  [1 1 1]
#  [2 2 2]
#  [2 2 2]]
x_train_all = np.concatenate([x_train_positive_all, x_train_negative_all], 0)

322


In [113]:
print(x_train_all)

[[[[ 0.000000e+00]
   [ 0.000000e+00]
   [ 0.000000e+00]
   ...
   [ 0.000000e+00]
   [ 0.000000e+00]
   [ 0.000000e+00]]

  [[-1.000000e+00]
   [-4.685494e-01]
   [ 1.630295e-01]
   ...
   [ 8.510911e-01]
   [ 1.630295e-01]
   [-2.554557e-01]]

  [[ 0.000000e+00]
   [ 0.000000e+00]
   [ 0.000000e+00]
   ...
   [ 0.000000e+00]
   [ 0.000000e+00]
   [ 0.000000e+00]]

  ...

  [[ 2.000000e+00]
   [ 1.000000e+00]
   [ 1.000000e+00]
   ...
   [ 1.000000e+00]
   [ 1.000000e+00]
   [ 1.000000e+00]]

  [[ 3.000000e+00]
   [ 3.000000e+00]
   [ 2.000000e+00]
   ...
   [ 2.000000e+00]
   [ 2.000000e+00]
   [ 2.000000e+00]]

  [[ 0.000000e+00]
   [ 0.000000e+00]
   [ 0.000000e+00]
   ...
   [ 0.000000e+00]
   [ 0.000000e+00]
   [ 0.000000e+00]]]


 [[[ 0.000000e+00]
   [ 0.000000e+00]
   [ 0.000000e+00]
   ...
   [ 0.000000e+00]
   [ 0.000000e+00]
   [ 0.000000e+00]]

  [[ 0.000000e+00]
   [ 0.000000e+00]
   [ 1.630295e-01]
   ...
   [ 1.000000e+00]
   [ 1.000000e+00]
   [ 1.630295e-01]]

  [[ 0.

In [ ]:
print(len(np.concatenate([x_train_positive_all_5crossval, x_train_negative_all_5crossval], 0)))
# [[1 1 1]
#  [1 1 1]
#  [2 2 2]
#  [2 2 2]]
x_train_all_5crossval = np.concatenate([x_train_positive_all_5crossval, x_train_negative_all_5crossval], 0)

In [114]:
y_train_negative_all =  np.array([[1.0, 0.0]]*len(x_train_negative_all))

In [115]:
y_train_negative_all_5crossval  = np.array([[1.0, 0.0]]*len(x_train_negative_all_5crossval))

In [116]:
print(len(np.concatenate([y_train_positive_all, y_train_negative_all], 0)))
# [[1 1 1]
#  [1 1 1]
#  [2 2 2]
#  [2 2 2]]
y_train_all = np.concatenate([y_train_positive_all, y_train_negative_all], 0)

322


In [118]:
print(len(np.concatenate([y_train_positive_all_5crossval, y_train_negative_all_5crossval], 0)))
# [[1 1 1]
#  [1 1 1]
#  [2 2 2]
#  [2 2 2]]
y_train_all_5crossval = np.concatenate([y_train_positive_all_5crossval, y_train_negative_all_5crossval], 0)

79


# 最終的なデータの保存

In [119]:
# saving numarray(ndarray)
np.save('../saving_numpy_array/v8-16/x_train/all/x_train_positive_all_v8-16', x_train_all)
np.save('../saving_numpy_array/v8-16/x_train/all/y_train_positive_all_v8-16', y_train__all)
np.save('../saving_numpy_array/v8-16/x_train/all/x_train_positive_all_ 5crossval_v8-16', x_train_all_5crossval)
np.save('../saving_numpy_array/v8-16/x_train/all/y_train_positive_all_5crossval_v8-16', y_train_all_5crossval)

In [ ]:
print(len(x_train_all))
print(len(x_train_all_5crossval))

print(len(y_train_all))
print(len(y_train_all_5crossval))

In [ ]:
#negative_data_sum_check = {}

In [61]:
'''
negative_data_sum_check = []
total = 0
for i in range(len(x_train_negative_all)):
    total = 0
    for j in range(14):
        for k in range(8):
            #print(a[j][k][0])
            total = total + x_train_negative_all[i][j][k][0]
    negative_data_sum_check.append(total)

SyntaxError: EOF while scanning triple-quoted string literal (<ipython-input-61-16c89d6f948d>, line 10)

In [ ]:
#print(negative_data_sum_check)

In [ ]:
#print(len(negative_data_sum_check))

In [ ]:
#print(list(set(negative_data_sum_check)))

In [32]:
print(len(list(set(negative_data_sum_check))))

151


In [22]:
#ndata_dic = {}
#ndata_dic[0] = x_train_negative_all[0]

In [23]:
#print(ndata_dic)

{0: array([[[  0.9997489],
        [  0.       ],
        [  0.9997489],
        [  0.999995 ],
        [  0.       ],
        [  0.9997489],
        [  0.999995 ],
        [  0.       ]],

       [[ -0.8510911],
        [  0.915276 ],
        [ -0.8510911],
        [ -0.7021823],
        [ -0.4685494],
        [ -0.8510911],
        [ -0.7021823],
        [  0.915276 ]],

       [[  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ]],

       [[  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ],
        [  0.       ]],

       [[146.19     ],
        [165.19     ],
        [146.19     ],
        [174.2      ],
        [105.09     ],
        [146.19     ],
        [174.2      ],
        [165.19     ]],

       [[128.18     ],
        [147.18     ],
        [128.18     

In [17]:
print(len(negative_data_sum_check))

189


In [ ]:
#random.shuffle(x_train_negative_all)

check what sequence to try create validataion data.

In [2]:
# check what sequence to try create validataion data.
print(x_train_negative_all)

NameError: name 'x_train_negative_all' is not defined

In [ ]:
#x_train_all_5crossval = np.append(x_train_all_5crossval, x_train_negative_all[:five_cross], 0)

In [ ]:
print(x_train_all_5crossval)

In [ ]:
print(len(x_train_all_5crossval))

# ここやってなかった．negative_dataの5crossvalも保存する．

In [25]:
np.save('../saving_numpy_array/v8-16/x_train/all/x_train_all_ 5crossval_v8-16_only_negative.npy', x_train_negative_all[:five_cross])

In [ ]:
#x_train_negative_all = np.delete(x_train_negative_all, slice(0, five_cross), 0)

In [ ]:
print(len(x_train_negative_all))

In [ ]:
y_train_all =  np.append(y_train_all, [[0.0, 1.0]]*len(x_train_negative_all), 0)

In [ ]:
print(len(y_train_all))

In [ ]:
y_train_all_5crossval  = np.append(y_train_all_5crossval, [[0.0, 1.0]]*five_cross, 0)

In [ ]:
print(y_train_all_5crossval)

In [ ]:
for i in range(len(y_train_all)):
    print(y_train_all[i])

In [ ]:
for i in range(len(y_train_all_5crossval)):
    print(y_train_all_5crossval[i])

In [ ]:
x_train_all = np.append(x_train_all, x_train_negative_all, 0)

In [ ]:
print(len(x_train_all))
print(len(x_train_all_5crossval))

print(len(y_train_all))
print(len(y_train_all_5crossval))

## saving ndarrray

In [ ]:
# saving numarray(ndarray)
np.save('./saving_numpy_array/v8-16/x_train/all/x_train_all_v8-16', x_train_all)
np.save('./saving_numpy_array/v8-16/x_train/all/y_train_all_v8-16', y_train_all)
np.save('./saving_numpy_array/v8-16/x_train/all/x_train_all_5crossval_v8-16', x_train_all_5crossval)
np.save('./saving_numpy_array/v8-16/x_train/all/y_train_all_5crossval_v8-16', y_train_all_5crossval)

In [ ]:
for i in range(len(x_train_all)):
    print(x_train_all[i])

In [ ]:
for i in range(len(y_train_all)):
    print(y_train_all[i])

In [ ]:
for i in range(len(x_train_all_5crossval)):
    print(x_train_all_5crossval[i])

In [ ]:
for i in range(len(y_train_all_5crossval)):
    print(y_train_all_5crossval[i])